# Αυτο-οργανούμενοι Χάρτες

Στο notebook αυτό θα χρησιμοποιήσουμε τη βιβλιοθήκη [Somoclu](https://somoclu.readthedocs.io/en/stable/index.html). Πρόκειται για μια σύγχρονη και βελτιστοποιημένη υλοποίηση των SOM, παραλληλοποιημένη για CPU και GPU. Πρώτα την εγκαθιστούμε:


In [ ]:
!pip install --upgrade somoclu

Επίσης, ενημερώνουμε στις τελευταίες εκδόσεις τους, τις υπόλοιπες βιβλιοθήκες που πρόκειται να χρησιμοποιοήσουμε

In [ ]:
!pip install --upgrade pip
!pip install --upgrade numpy
!pip install --upgrade pandas
!pip install --upgrade scikit-learn

## Εισαγωγή βιβλιοθηκών

Εισάγουμε numpy, matplotlib και mpl_toolkits, και somoclu:

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import somoclu
%matplotlib inline

## Δημιουργία και οπτικοποίηση δεδομένων

Δημιουργούμε 3 τεχνητές ομάδες τρισδιάστατων δεδομένων και εμφανίζουμε το γράφημα αναπαράστασής τους με διαφορετικό χρώμα για κάθε ομάδα:

In [ ]:
samples_in_each_class = 200
c1 = np.random.rand(samples_in_each_class, 3)/5
c2 = (0.6, 0.1, 0.05) + np.random.rand(samples_in_each_class, 3)/5
c3 = (0.4, 0.1, 0.7) + np.random.rand(samples_in_each_class, 3)/5
data = np.float32(np.concatenate((c1, c2, c3)))
colors = ["red"] * samples_in_each_class
colors.extend(["green"] * samples_in_each_class)
colors.extend(["blue"] * samples_in_each_class)
fig = plt.figure()
ax = Axes3D(fig)
ax.scatter(data[:, 0], data[:, 1], data[:, 2], c=colors)
labels = range(3*samples_in_each_class)

## Αρχικοποίηση και εκπαίδευση του SOM
Στη συνέχεια αρχικοποιούμε ένα χάρτη SOM με 10 x 10 νευρώνες και τον εκπαιδεύουμε με default παραμέτρους. Χρησιμοποιούμε τη magic `time` για να πάρουμε το χρόνο εκπαίδευσης.

In [ ]:
n_rows, n_columns = 10, 10
som = somoclu.Somoclu(n_columns, n_rows, compactsupport=False)
%time som.train(data)

Δείτε [εδώ](https://somoclu.readthedocs.io/en/stable/reference.html) όλο το function reference της βιβλιοθήκης.

## Απεικόνιση SOM

Η βιβλιοθήκη προσφέρει διάφορες δυνατότητες απεικόνισης του χάρτη.

### Επίπεδα συνιστωσών

H πρώτη είναι να δούμε τα επίπεδα συνιστωσών (component planes), ως προς τους (τρεις) άξονες των διαστάσεων εισόδου. To colorbar μας δείχνει ποιοι νευρώνες του codebook (δηλαδή των 10x10 νευρώνων εξόδου) είναι κοντά. Θυμόμαστε ότι οι νευρώνες εξόδου βρίσκονται σε χώρο ίδιων διαστάσεων με τα διανύσματα εισόδου. Τα 3 γραφήματα είναι για x, y και z.

In [ ]:
som.view_component_planes(colorbar=True, bestmatches=True, figsize=(15, 15))

Η figsize ελέγχει τις διαστάσεις του γραφήματος (zoom), όχι τις διαστάσεις του grid.

Η απεικόνιση με επίπεδα συνιστωσών είναι πολύ αναλυτική, περισσότερο από ότι θα χρειαζόταν για να μας βοηθήσει στην ομαδοποίηση.

### U-matrix

Στην πράξη χρησιμοποιούμε το U-matrix που μας δείχνει το πλέγμα του SOM και το χρωματίζει ανάλογα το πόσο απέχουν οι νευρώνες εξόδου μεταξύ τους (όπως είδαμε στο μάθημα και σύμφωνα με το colorbar)

In [ ]:
som.view_umatrix(bestmatches=True, bestmatchcolors=colors, labels=labels, colorbar=True, figsize=(15, 15))

## Παρατηρήσεις για την απεικόνιση U-matrix

- με `bestmatches=True` και `labels=labels` τυπώνουμε τα labels των δειγμάτων εισόδου που ανήκουν σε κάθε νευρώνα νικήτη (best matching unit - bmu). Προσοχή εδώ, στο local install του Somoclu ο χάρτης είναι διαδραστικός, στο notebook οχι. Προφανώς δεν ανήκει μόνο ένα δείγμα εισόδου σε κάθε bmu όπως φαίνεται εδώ αφου έχουμε 100 bmus και samples_in_each_class x 3 δείγματα εισόδου (πχ  600 για samples_in_each_class=200). Ο λόγος που εμφανίζεται έτσι είναι γιατί εμφανίζεται μόνο η ετικέτα του τελευταίου δείγματος που ανατίθεται στο κάθε bmu (φανταστείτε δηλαδή ότι κάτω από κάθε ετικέτα συνήθως υπάρχουν και άλλες).
- Οι κόκκινες περιοχές δείχνουν περιοχές με μεγάλες αποστάσεις και οι μπλε περιοχές δείχνουν περιοχές με μικρές αποστάσεις. Εποπτικά, βλέπουμε ότι έχει διαχωρίσει καλά σε τρία clusters τα δείγματα εισόδου. 

## Clustering των νευρώνων νικητών (bmus)
Η `bestmatchcolors=colors` βάζει χρώμα στα bmu που ανήκουν στο ίδιο cluster. Αυτό δεν γίνεται εποπτικά ("με το μάτι" από το U-matrix) αλλά ως εξής σε τρια βήματα:  
1. μέσω ανταγωνιστικής μάθησης έχουμε μάθει τα βάρη των νευρώνων νικητών (bmus). 
2. εφαρμόζουμε έναν αλγόριθμο συσταδοποίησης όπως k-means για βρούμε ποιοι νευρώνες νικητές ανήκουν στο ίδιο cluster
3. χρωματίζουμε με το ίδιο χρώμα τους νευρώνες κάθε cluster

Μπορούμε να ορίσουμε όποιον αλγόριθμο συσταδοποίησης θέλουμε για τα bmus του SOM:
```python
from sklearn.cluster import KMeans
algorithm = KMeans()
som.cluster(algorithm=algorithm)
```

### Best matching units (BMUS)

Μπορούμε να δούμε σε ποιο νευρώνα νικητή ανήκει κάθε δείγμα εισόδου ως εξής:

In [ ]:
bmus = som.bmus

In [ ]:
print(bmus.shape)

οι διαστάσεις είναι τα διανύσματα εισόδου επί τις διαστάσεις του πλέγματός μας (2 εφόσον είναι 10x10). Ο πίνακας bmus μας δείχνει τις συντεταγμένες στο πλέγμα του νευρώνα νικητή στον οποίο ανήκει το κάθε δείγμα εισόδου.

In [ ]:
print(bmus)

**Προσοχή**
- η σύμβαση του Somoclu είναι \[κολόνα γραμμή\] (ανάποδα από την Python)
- αν πάρετε τις μοναδικές εμφανίσεις των bmus μπορεί να είναι λιγότερες από 100 (10x10). Αυτό γιατί μπορεί να υπάρξουν νευρώνες εξόδου που δεν νίκησαν ποτέ και δεν τους έχουν ανατεθεί δείγματα εδώ.

Μπορούμε να απαριθμήσουμε τα μοναδικά bmus και να πάρουμε άνα πίνακα που μας δείχνει σε ποιο αριθμό bmu ανήκει κάθε δείγμα εισόδου ως εξής:

In [ ]:
ubmus, indices = np.unique(bmus, return_inverse=True, axis=0)
# το return_inverse επιστρέφει και τους δείκτες indices

Τυπώνουμε τα μοναδικά bmus. Το \[0 0\] είναι το bmu 0, το \[0 1\] είναι το bmu 1, το \[0 2\] είναι το bmu 2  κοκ. 

In [ ]:
print(ubmus)

Τυπώνουμε τέλος για κάθε δείγμα εισόδου σε ποιο αριθμό bmu ανήκει. (πιο βολικό από τις συντεταγμένες των bmus)

In [ ]:
print(indices)